In [17]:
palette={'black': '#000000', 'vermillion': '#E69F00',
'blue': '#56B4E9', 'green': '#009E73','orange': '#D55E00',
'yellow': '#F0E442', 'red': '#CC79A7','darkgrey':'#2F4F4F'}

poly_color=palette['blue']

In [2]:
from phidl.geometry import Device
import phidl.geometry as pg
from phidl.quickplotter import quickplot2 as qp2
import matplotlib.pyplot as plt
from matplotlib.patches import Polygon
from phidl.path import Path,CrossSection
import shapely
%matplotlib qt

In [3]:
import numpy as np
import os
os.getcwd()

'/home/csaba/Documents/nature_protocol'

In [4]:
fig=plt.figure()
ax=fig.add_axes((0,0,1,1))
ax.set_axis_off()
ax.set_aspect('equal')


from phidl.geometry import Device
import numpy as np
#pear_drop quartic
a,b=1,3
x=np.linspace(0,a,200)
y=np.sqrt(x**3*(a-x))/b
x_full=np.hstack((x,x[::-1]))
y_full=np.hstack((y,-y[::-1]))

form=Device()
form.add_polygon([x_full,y_full])
form.write_gds('teardrop.gds')


#ax.plot(x[::10],y[::10],'o',markersize=1)
from matplotlib.patches import Polygon
ax.add_patch(Polygon(np.vstack((x_full,y_full,)).T,fc=poly_color))

#Fermat spiral
a=.05
t=np.linspace(0,8*np.pi,1000)
r=np.concatenate([a*np.sqrt(t[::-1]),-(a*np.sqrt(t))])
full_t=np.concatenate([t[::-1],t])
x=np.cos(full_t)*r+.5
y=np.sin(full_t)*r+.5
ax.plot(x,y,linewidth=2,color=poly_color)
plt.savefig('fig1a.svg')
help(ax.get_tightbbox)

Help on method get_tightbbox in module matplotlib.axes._base:

get_tightbbox(renderer=None, call_axes_locator=True, bbox_extra_artists=None, *, for_layout_only=False) method of matplotlib.axes._axes.Axes instance
    Return the tight bounding box of the Axes, including axis and their
    decorators (xlabel, title, etc).
    
    Artists that have ``artist.set_in_layout(False)`` are not included
    in the bbox.
    
    Parameters
    ----------
    renderer : `.RendererBase` subclass
        renderer that will be used to draw the figures (i.e.
        ``fig.canvas.get_renderer()``)
    
    bbox_extra_artists : list of `.Artist` or ``None``
        List of artists to include in the tight bounding box.  If
        ``None`` (default), then all artist children of the Axes are
        included in the tight bounding box.
    
    call_axes_locator : bool, default: True
        If *call_axes_locator* is ``False``, it does not call the
        ``_axes_locator`` attribute, which is necessary 

In [5]:
qp2(form)

In [6]:
def connector(end_width,hollow_radius,length_armlet,n_arms):
    def rotate(xy,angle):
        c=np.cos(angle/180.*np.pi)
        s=np.sin(angle/180.*np.pi)
        mat=np.array([[c,-s],[s,c]])
        return np.matmul(mat,xy.T).T
    rot_ang=360./n_arms
    p1=np.array([end_width/2.,length_armlet]) #right point of top arm
    p2=rotate(np.array([-end_width/2.,length_armlet]),-rot_ang)#left point of next arm

    p1_rotback,p2_rotback = [rotate(p,rot_ang/2) for p in [p1,p2]] #rotate back into a convenient frame, i.e put things back to vertical
    circle_cut_center = np.array([0,p1_rotback[1]+np.sqrt(hollow_radius**2-p1_rotback[0]**2)])
    angle_start = np.arctan2(*np.array(p1_rotback-circle_cut_center)[::-1])
    sector =2*np.arcsin(p1_rotback[0]/hollow_radius)
    t=np.linspace(angle_start,angle_start-sector,100)
    circular_cut=np.array([np.cos(t)*hollow_radius,np.sin(t)*hollow_radius])+circle_cut_center.reshape(2,1)
    circular_cut=rotate(circular_cut.T,-rot_ang/2).T #rotate back to original frame
    polygons=[rotate(circular_cut.T,-rot_ang*n) for n in range(n_arms)]
    print(rot_ang)
    return np.concatenate(polygons)
connectors=[connector(15,180,125,3),connector(15,100,125,4),connector(15,75,125,5),connector(15,60,125,6)]

fig,ax=plt.subplots(1,1,figsize=(5,5))
for i in range(2):
    for j in range(2):
        
        ax.add_patch(Polygon(connectors[2*i+j]+np.asarray([[i*350,j*350]]),fc=poly_color))
        ax.set_aspect('equal')
        ax.set_axis_off()
ax.set_xlim(-136,480)
ax.set_ylim(-100,480)
plt.savefig('fig1b.svg')

120.0
90.0
72.0
60.0


In [7]:
plt.close('all')

In [8]:
def smooth_boolean(device,radius):
    '''
    device is phidle.geometry.Device()
    radius is a float, >0, determining the curvature radius of smoothened concave corners'''
    
    polygons=device.get_polygons()
    if len(polygons)==1:
        polygon=shapely.Polygon(polygons[0])
    else:
        polygon=shapely.Polygon(polygons[0])
        for i in range(1,len(polygons)):
            pi = shapely.Polygon(polygons[i])
            polygon=polygon.union(pi)
    #implement warnings in case pol1,pol2 are not (n,2)....
    pol_round=polygon.buffer(radius).buffer(-radius)
    def make_to_phidl_dev(pol_round):
        rounded=pg.Device()
        rounded.add_polygon( np.asarray(pol_round.exterior.coords))
        if len(pol_round.interiors)>0:
            interior=pg.Device()
            for hole in pol_round.interiors:
                interior.add_polygon(hole.coords)
            rounded=pg.boolean(rounded,interior,operation='A-B')
        return rounded
    #gotta split multipolygon in individual polygons to get exterior/interior primitives
    if pol_round.geom_type=='MultiPolygon':
        collect_dev = pg.Device()
        for pol in pol_round.geoms:
            collect_dev<<make_to_phidl_dev(pol)
    else:
        collect_dev=make_to_phidl_dev(pol_round)
    return collect_dev

In [9]:
dev=pg.ring(radius=75,width=20)
for rot in range(0,360,120):
    dev<<pg.rectangle(size=(150,10)).movex(-75).movey(-5).rotate(rot)
smooth_dev = smooth_boolean(dev,10)

In [10]:
fig,ax=plt.subplots(1,1,figsize=(5,5))
for idx,p in enumerate(dev.get_polygons()):
    ax.add_patch(Polygon(p,ec='k',linestyle='dashed',color=[poly_color,palette['vermillion'],palette['red'],palette['green']][idx]))
ax.set_xlim(-90,280)
ax.set_ylim(-90,90)
ax.add_patch(Polygon(smooth_dev.get_polygons()[0]+np.array([190,0]),color=poly_color))
ax.set_aspect('equal')
ax.set_axis_off()
plt.savefig('fig1c.svg')

In [11]:
plt.close('all')

In [13]:
def get_norm(arr):
    '''arr shape = (n,2)'''
    nxy = np.gradient(arr,axis=0)
    nxy /= np.sqrt(np.sum(nxy**2,axis=1)).reshape(-1,1)
    return nxy[:,::-1]*np.array([[1,-1]]) #(dy,-dx)


In [19]:
fig,ax=plt.subplots(1,1,figsize=(5,5))

c1 = pg.circle(radius=50)
c2 = pg.circle(radius=90).movex(210).movey(90)

for c in [c1,c2]:
    ax.add_patch(Polygon(c1.get_polygons()[0],zorder=0,color=poly_color))#,ec='k',linestyle='dashed'))
    ax.add_patch(Polygon(c2.get_polygons()[0],zorder=0,color=poly_color))#,ec='k',linestyle='dashed'))

ax.set_xlim(0,140)
ax.set_ylim(10,80)

from geomdl import NURBS

# Create a 3-dimensional B-spline Curve
curve = NURBS.Curve()

# Set degree
curve.degree = 3



# Set control points (weights vector will be 1 by default)
# Use curve.ctrlptsw is if you are using homogeneous points as Pw
c1xy,c2xy=[pol.get_polygons()[0] for pol in [c1,c2]]
n1xy,n2xy=[get_norm(p) for p in [c1xy,c2xy]]
m,s=35,45
p1,p2,p3,p4=c1xy[18],c1xy[18]+m*n1xy[18],c2xy[85]+s*n2xy[85],c2xy[85]
curve.ctrlpts = [p1,p2,p3,p4]

# Set knot vector
curve.knotvector = [0, 0, 0, 0, 1, 1, 1, 1]

# Set evaluation delta (controls the number of curve points)
curve.delta = 0.01

# Get curve points (the curve will be automatically evaluated)
curve_points = np.asarray(curve.evalpts)[:,:]

p=Path(curve_points)
X=CrossSection()
X.add(width=5)
pth=p.extrude(X).get_polygons()[0]

d=pg.Device()
for p in [c1,c2,p.extrude(X)]:
    d<<p
latch=pg.boolean(smooth_boolean(d,radius=5),pg.boolean(c1,c2,operation='A+B'),operation=('A-B'))
latch_pol=latch.get_polygons()[np.argmax([len(el) for el in latch.get_polygons()])]
ax.add_patch(Polygon(latch_pol,ec='k',linewidth=1,zorder=1,color=palette['red']))
ax.plot(curve_points[:,0],curve_points[:,1],linestyle='dashed',zorder=2,color='k')
for idx,p in enumerate(curve.ctrlpts):
    plt.plot(p[0],p[1],'o',color='k')
    plt.text(p[0]-5,p[1]+(-1)**(idx//2)*7,r'$\vec{p}_'+str(idx+1)+'$')
plt.plot(*np.asarray(curve.ctrlpts).T,'--',linewidth=.5)
ax.set_axis_off()
ax.set_aspect('equal')
plt.savefig('fig1d.svg',transparent=True)

In [98]:
curve.ctrlpts[:,0]

TypeError: list indices must be integers or slices, not tuple

In [106]:
n_ondulation = [16, 16, 8]
rs = [550, 320, 120]
r_mod = [0.06, 0.06, 0.06]
thicknesses = [25,15,10]

dev=pg.Device()
polys=[]
connection_areas=pg.Device()
connection_area_rad=35

for idx, (rad, thick) in enumerate(zip(rs, thicknesses)):
    r = rad + r_mod[idx] * rad * np.sin(np.linspace(0, n_ondulation[idx] * 2 * np.pi, 512))
    initial_rot = 30
    t = np.linspace(0, 2 * np.pi, 512) + initial_rot
    x, y = r * np.cos(t), r * np.sin(t)
    plt.plot(x,y)
    pth = Path(np.vstack([x,y]).T)
    X=CrossSection()
    X.add(width=thick)
    dev<<smooth_boolean(pth.extrude(X),radius=20)
    polys.append(np.vstack((x,y)).T)

paths=pg.Device()
for idx,n in enumerate([16,8]):
    for latch in range(n):
        x0,y0 = polys[idx][len(polys[idx])//n*latch]
        xe,ye = polys[idx+1][(len(polys[idx+1])//n*latch+65)%len(polys[idx+1])]
        
        connection_areas<<pg.circle(radius=connection_area_rad).movex(xe).movey(ye)
        connection_areas<<pg.circle(radius=connection_area_rad).movex(x0).movey(y0)

        
        r0,re = np.sqrt(x0*x0+y0*y0),np.sqrt(xe*xe+ye*ye)
        t0,te = np.arctan2(y0,x0),np.arctan2(ye,xe)
        if (te-t0)<0: #looping the other way around
            t0-=2*np.pi
        t=np.linspace(t0,te,100)
        rz=np.linspace(0,1,100)*(re-r0)+r0
        x_latch,y_latch = rz*np.cos(t),rz*np.sin(t)
        plt.plot(x_latch,y_latch)
        X=CrossSection()
        X.add(width=10)
        paths<<Path(np.vstack((x_latch,y_latch)).T).extrude(X)
joined_dev = pg.boolean(dev,paths,operation='A+B')
        
smooth_connections = pg.boolean(joined_dev,connection_areas,operation='AND') #cut out contact areas
smooth_connections=smooth_boolean( smooth_connections, radius=20)
final_dev = smooth_boolean( pg.boolean(smooth_connections,joined_dev,operation='A+B'), radius=5)

In [107]:
qp2(final_dev)

In [14]:
def device_to_shapely_pol(dev):
    pols=dev.get_polygons()
    sh_pol = shapely.Polygon(pols[0])
    if len(pols)==1:
        return sh_pol
    else:
        for p in pols[1:]:
            sh_pol = sh_pol.union(shapely.Polygon(p))
        return sh_pol

In [15]:
fig,ax=plt.subplots(1,1,figsize=(5,5))
for p in final_dev.get_polygons():
    ax.add_patch(Polygon(p,color=poly_color))
ax.set_xlim(-600,600)
ax.set_ylim(-600,600)
ax.set_axis_off()
plt.savefig('fig1e.svg',transparent=True)

In [16]:
shapelypolygon = device_to_shapely_pol(final_dev)

def reshape(d,scale):
    from scipy.interpolate import interp1d
    #d is a polygon
    x,y=d.T
    s=np.cumsum( np.hstack( (0,np.sqrt(np.diff(x)**2+np.diff(y)**2)) ) )
    total_length=s[-1]
    s=s/s[-1]
    #scale=15 #microns
    fx=interp1d(s,x)
    fy=interp1d(s,y)
    new_s = np.linspace(0,1,int(total_length/scale))
    ix,iy=fx(new_s),fy(new_s)
#     plt.scatter(*d.T)
#     plt.scatter(ix,iy,s=0.1)
    return np.vstack((ix,iy)).T

In [17]:
geometry= pygmsh.occ.Geometry()
model = geometry.__enter__()

outer_points= reshape(np.asarray(shapelypolygon.exterior.coords)[:-1,:],15)

outpts = [model.add_point( (el[0],el[1],0)) for el in outer_points]
outer_line = [model.add_line(outpts[i], outpts[i + 1]) for i in range(-1, len(outpts) - 1)]
outer_loop = model.add_curve_loop(outer_line)

inner_loops = []
for g in shapelypolygon.interiors:
    inner_points = reshape(np.asarray(g.coords)[:-1,:],15)
    inpts = [model.add_point( (el[0],el[1],0)) for el in inner_points]
    inner_line = [model.add_line(inpts[i], inpts[i + 1]) for i in range(-1, len(inpts) - 1)]
    inner_loop = model.add_curve_loop(inner_line)
    inner_loops.append(inner_loop)
plane_surface = model.add_plane_surface(outer_loop, holes=inner_loops)

model.synchronize()

volume_marker=2
model.add_physical(outer_loop.curves,"Boundary")

geometry.generate_mesh(dim=2)

NameError: name 'pygmsh' is not defined

In [137]:
for cell in mesh.cells:
    if cell.type == "triangle":
        triangle_cells = cell.data
    elif  cell.type == "tetra":
        tetra_cells = cell.data
import meshio
triangle_mesh =meshio.Mesh(points=mesh.points[:,:2]/(2*np.max(mesh.points)),
                           cells=[("triangle", triangle_cells)],
                           cell_data={"name_to_read":[np.zeros( (len(triangle_cells),3))]})
meshio.write("/home/csaba/fenics-shells/mesh.xdmf", triangle_mesh)


In [136]:
mesh.cells[0].data

array([[ 280,    0],
       [   0,    1],
       [   1,    2],
       ...,
       [1977, 1978],
       [1978, 1979],
       [1979, 1980]], dtype=uint64)

In [131]:
def create_mesh(mesh, cell_type, prune_z=False):
    cells = mesh.get_cells_type(cell_type)
    cell_data = mesh.get_cell_data("gmsh:physical", cell_type)
    points = mesh.points[:, :2] if prune_z else mesh.points
    out_mesh = meshio.Mesh(
        points=points, cells={cell_type: cells}, cell_data={"name_to_read": [cell_data]}
    )
    return out_mesh
create_mesh(mesh, "triangle", prune_z=True)

KeyError: 'gmsh:physical'

In [115]:
resolution = 0.01
# Channel parameters
L = 2.2
H = 0.41
c = [0.2, 0.2, 0]
r = 0.05

# Initialize empty geometry using the build in kernel in GMSH
geometry = pygmsh.geo.Geometry()
# Fetch model we would like to add data to
model = geometry.__enter__()
# Add circle
circle = model.add_circle(c, r, mesh_size=resolution)
# Add points with finer resolution on left side
points = [
    model.add_point((0, 0, 0), mesh_size=resolution),
    model.add_point((L, 0, 0), mesh_size=5 * resolution),
    model.add_point((L, H, 0), mesh_size=5 * resolution),
    model.add_point((0, H, 0), mesh_size=resolution),
]

# Add lines between all points creating the rectangle
channel_lines = [
    model.add_line(points[i], points[i + 1]) for i in range(-1, len(points) - 1)
]

# Create a line loop and plane surface for meshing
channel_loop = model.add_curve_loop(channel_lines)
plane_surface = model.add_plane_surface(channel_loop, holes=[circle.curve_loop])

# Call gmsh kernel before add physical entities
model.synchronize()
volume_marker = 6
model.add_physical([plane_surface], "Volume")
model.add_physical([channel_lines[0]], "Inflow")
model.add_physical([channel_lines[2]], "Outflow")
model.add_physical([channel_lines[1], channel_lines[3]], "Walls")
model.add_physical(circle.curve_loop.curves, "Obstacle")
geometry.generate_mesh(dim=2)
gmsh.write("mesh.msh")
gmsh.clear()
geometry.__exit__()
mesh_from_file = meshio.read("mesh.msh")
triangle_mesh = create_mesh(mesh_from_file, "triangle", prune_z=True)
meshio.write("mesh.xdmf", triangle_mesh)

mesh_from_file.cell_data

{'gmsh:physical': [array([5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5]),
  array([5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5]),
  array([5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5]),
  array([2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
         2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]),
  array([4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4]),
  array([3, 3, 3, 3, 3, 3, 3, 3, 3]),
  array([4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4]),
  array([1, 1, 1, ..., 1, 1, 1])],
 'gmsh:

In [127]:
x,y,_=mesh.points.T
quads=mesh.cells[1].data

qdev_map=pg.Device()
for q in quads:
    qdev_map.add_polygon(np.vstack((x[q],y[q])).T)
qp2(qdev_map)

/home/csaba/anaconda3/lib/python3.12/site-packages/phidl/quickplotter.py:959: UserWarning: [PHIDL] Warning: `quickplot2` will be removed in April 2025, please replace with quickplot() 
  warnings.warn(


In [65]:
import pygmsh
import gmsh
with pygmsh.occ.Geometry() as geom:
    perimeter=geom.add_polygon(np.asarray(shapelypolygon.exterior.coords)[:-1,:]) 
    #holes= [geom.add_polygon(reshape(d,45)) for d in neg_holes.get_polygons()]
    holes = [geom.add_polygon(np.asarray(interior.coords)[:-1,:])
             for interior in shapelypolygon.interiors]
    geom.boolean_difference(perimeter, holes)
   # gmsh.option.setNumber('Mesh.Algorithm',1)
    gmsh.option.setNumber("Mesh.MeshSizeMin", 15)

#     gmsh.option.setNumber('Mesh.Smoothing',1)
#     gmsh.option.setNumber('Mesh.SubdivisionAlgorithm', 1)
#     gmsh.option.setNumber('Mesh.RecombineAll', 1)
    mesh =geom.generate_mesh()

In [66]:
x,y,_=mesh.points.T
quads=mesh.cells[1].data

qdev_map=pg.Device()
for q in quads:
    qdev_map.add_polygon(np.vstack((x[q],y[q])).T)
qp2(qdev_map)

In [67]:
shapelypolygon = device_to_shapely_pol(final_dev)
resolution = 5
all_exteriors=[]
for i in range(2):
    for interior in shapelypolygon.interiors:
        if i==0:
            x,y=np.asarray(interior.coords).T
            plt.plot(x,y,color='r')
        fluffed_interior = shapely.Polygon(interior.coords).buffer(resolution*(i+1))
        fluffed_interior = shapelypolygon.intersection(fluffed_interior)
        if fluffed_interior.geom_type!='MultiPolygon':
            x,y=np.asarray(fluffed_interior.exterior.coords).T
            all_exteriors.append(fluffed_interior.exterior)
            plt.plot(x,y,color='k')
for i in range(5):
    reduced_exterior=shapely.Polygon(shapelypolygon.exterior.coords).buffer(-(resolution*(i+1))).exterior
    if shapelypolygon.contains(reduced_exterior):
        x,y=np.asarray(reduced_exterior.coords).T
        all_exteriors.append(reduced_exterior)
        plt.plot(x,y,color='g')
x,y=np.asarray(shapelypolygon.exterior.coords).T
plt.plot(x,y,color='r')

In [68]:
from shapely.ops import unary_union
unary_union(all_exteriors)

In [69]:
split_lines=shapely.unary_union(all_exteriors,grid_size=0.5)
split_lines_smooth=shapely.line_merge(split_lines)
len(split_lines.geoms),len(split_lines_smooth.geoms)

(23875, 2065)

In [70]:
import shapely
shapely.__version__

'2.0.6'

In [71]:
for s in split_lines_smooth.geoms:
    x,y=np.asarray(s.coords).T
    plt.plot(x,y)

In [72]:
intersects=[]
for i in range(len(all_exteriors)):
    tmp=all_exteriors[i].intersection(all_exteriors[i+1:])
    intersects+=[g for g in tmp if ((g.geom_type=='Point') or (g.geom_type=='MultiPoint')) ]

In [73]:
spliced=[]
for a in all_exteriors:
    diff=shapely.difference(a,intersects)
    if len(diff)>0:
        spliced.append(diff)

In [74]:
for a in all_exteriors[0].difference(intersects):
    x,y=np.asarray(a.coords).T
    plt.plot(x,y)

In [75]:
for i in range(len(all_exteriors)):
    for geom in all_exteriors[i].intersection(all_exteriors[i+1:]):

        try:
            if hasattr(geom,'coords'):
                x,y=np.asarray(geom.coords).T
                plt.plot(x,y,'o',color='r')
        except:
            for g in geom.geoms:
                x,y=np.asarray(g.coords).T
                plt.plot(x,y,'o',color='r')
#np.unique(gtypes)

In [76]:
for i in intersects:
    i.coords

NotImplementedError: Sub-geometries may have coordinate sequences, but multi-part geometries do not

In [ ]:
from shapely.ops import unary_union
unioned_path=unary_union([el.buffer(1) for el in all_exteriors])
#unioned_path=unioned_path.buffer(1).buffer(-.9)
unioned_path

In [ ]:
def make_to_phidl_dev(pol_round):
        rounded=pg.Device()
        rounded.add_polygon( np.asarray(pol_round.exterior.coords))
        if len(pol_round.interiors)>0:
            interior=pg.Device()
            for hole in pol_round.interiors:
                interior.add_polygon(hole.coords)
            rounded=pg.boolean(rounded,interior,operation='A-B')
        return rounded
dev=make_to_phidl_dev(unioned_path)

In [ ]:
qp2(dev)

In [ ]:
outp=shapely.ops.linemerge(all_exteriors)
outp=shapely.set_precision(outp,1)
for o in outp.geoms:
    x,y=np.asarray(o.coords).T
    plt.plot(x,y)

In [ ]:
from centerline.geometry import Centerline
#cline=Centerline(unioned_path)
cline=Centerline(shapelypolygon)

In [ ]:
outp=shapely.ops.linemerge(cline.geometry)

In [ ]:
for o in outp.geoms:
    x,y=np.asarray(o.coords).T
    plt.plot(x,y)

In [ ]:
from scipy.spatial import cKDTree
def clean_skeleton_dangle(skeleton):
    '''skeleton is a shapely multiline'''
    xy_s=[]
    for line in skeleton.geoms:
        for g in line.boundary.geoms:
            p=np.asarray(g.coords).T
            xy_s.append(p)
    xy_s=np.asarray(xy_s)[:,:,0] #kill last dimension
    tree=cKDTree(xy_s)
    points_with_neighbors=np.unique(np.concatenate(list(tree.query_pairs(r=1e-5)))) 
    points_without_neighbors = [el//2 for el in range(2*len(skeleton.geoms)) if el not in points_with_neighbors]
    #we collect 2 points for each line edges in the kdtree, so line indices (who dangle) are obtained by //2
    new_skeleton=[skeleton.geoms[el] for el in range(len(skeleton.geoms)) if el not in points_without_neighbors]
    return shapely.MultiLineString(new_skeleton)

In [ ]:
midline_polygon=clean_skeleton_dangle(outp).buffer(.1)
midline_polygon

In [ ]:
dev1=make_to_phidl_dev(midline_polygon)
dev2=make_to_phidl_dev(shapelypolygon)

In [ ]:
holes=[shapely.Polygon(el) for el in shapelypolygon.interiors]

In [ ]:
collect=[]
distance=3
for i in np.arange(distance,10*distance,distance):
    for pol in midline_polygon.interiors:
        route_line=shapely.Polygon(pol).buffer(-i).buffer(-5).buffer(5) #Make line to polygon, buffer it down, grab its outline
        if (route_line.geom_type!='MultiPolygon'):
            if shapelypolygon.contains(route_line.exterior):
                collect.append(np.asarray(route_line.exterior.coords))
            else:
                left_over_line=route_line.exterior.intersection(shapelypolygon)
                xys=get_coords(left_over_line)
                if type(xys)==list:
                    for coords in xys:
                        collect.append(coords)
                elif len(xys)>0:
                    collect.append(xys)
            
        #     collect.append(np.asarray( shapelypolygon.difference(shapely.Polygon(route_line)).exterior.coords))
    route_line=shapely.Polygon(midline_polygon.exterior).buffer(i).buffer(5).buffer(-5).exterior #Make line to polygon, buffer it down, grab its outline
    if shapelypolygon.contains(route_line):
        collect.append(np.asarray(route_line.coords))

path_dev=pg.Device()
X=CrossSection()

X.add(width=.2)
for idx,p in enumerate(collect):
    path_dev<<Path(p).extrude(X)

In [ ]:
np.arange(5,3*5,5)

In [ ]:
for idx,p in enumerate(collect):
    plt.plot(p[:,0],p[:,1],color='r')

In [ ]:
def get_coords(obj):
    if hasattr(obj,'geoms'):
        coords=[]
        for g in obj.geoms:
            coords.append(np.asarray(g.coords))
    else:
        coords=np.asarray(obj.coords)
    return coords


In [ ]:
tmp=pg.Device()
tmp<<final_dev
tmp<<dev1.remap_layers({0:2})
tmp<<path_dev.remap_layers({0:5})
qp2(tmp)

In [ ]:
skel=clean_skeleton_dangle(outp)


In [ ]:
for g in skel.boundary.geoms:
    x,y=np.asarray(g.coords).T
    plt.plot(x,y,'o',color='r')

In [ ]:
# import meshio


# obj_mesh = meshio.Mesh(
#     points=mesh.points,
#     cells={'triangle':mesh.cells[1].data},
# )
# obj_mesh.write(
#     "dev.obj",  # str, os.PathLike, or buffer/open file
#     # file_format="vtk",  # optional if first argument is a path; inferred from extension
# )

In [ ]:
# mesh=meshio.read("devquad.obj")
# x,y,_=mesh.points.T
# quads=mesh.cells[0].data

# qdev_map=pg.Device()
# for q in quads:
#     qdev_map.add_polygon(np.vstack((x[q],y[q])).T)
# qp2(qdev_map)

In [ ]:
routes=shapely.MultiLineString([shapely.LineString(el) for el in collect])
routes=routes.union(skel)
waypoint=skel.boundary.geoms[0].buffer(20)
close_by_routes=waypoint.intersection(routes)
close_by_polygon_lines=close_by_routes.buffer(0.1)

In [ ]:
cutline=np.asarray(close_by_routes.geoms[0].coords)
len(cutline)

In [ ]:
import pygmsh
import gmsh
with pygmsh.occ.Geometry() as geom:
    perimeter=geom.add_polygon( reshape( np.asarray(waypoint.exterior.coords)[:-1,:],5))
    for i in range(len(cutline)-1):
        p1=geom.add_point((cutline[i,0],cutline[i,1]))
        p2=geom.add_point((cutline[i+1,0],cutline[i+1,1]))
        line=geom.add_line(p1,p2)

    #points=[geom.add_point((-1+0.1*i,0)) for i in range(20)]
    #cut=geom.add_polygon([[-1+0.1,0] for i in range(20)])
#    holes= [geom.add_polygon( reshape(np.asarray(polyg.exterior.coords)[:-1,:],5)) for polyg in close_by_polygon_lines.geoms]
#     holes = [geom.add_polygon(reshape(np.asarray(interior.coords)[:-1,:],5))
#              for interior in shapelypolygon.interiors]
    
    #geom.boolean_difference(perimeter, holes)
    gmsh.option.setNumber('Mesh.Algorithm',1)
    #gmsh.option.setNumber('Mesh.Resolution',5)
    #gmsh.option.setNumber('Mesh.Smoothing',1)
    #gmsh.option.setNumber('Mesh.SubdivisionAlgorithm', 1)
    gmsh.option.setNumber('Mesh.RecombineAll', 1)
    mesh =geom.generate_mesh()

In [ ]:
x,y,_=mesh.points.T
quads=mesh.cells[1].data

qdev_map=pg.Device()
for q in quads:
    qdev_map.add_polygon(np.vstack((x[q],y[q])).T)
qp2(qdev_map)

In [ ]:
total=close_by_routes.union(shapely.affinity.rotate(close_by_routes,180,origin=skel.boundary.geoms[0]))

In [ ]:
for l in clean_skeleton_dangle(total).geoms:
    x,y=np.asarray(l.coords).T
    plt.plot(x,y,color='b')
for c in collect:
    plt.plot(c[:,0],c[:,1],color='k')
for l in skel.geoms:
    x,y=np.asarray(l.coords).T
    plt.plot(x,y,color='k')
plt.xlim(-600,-500)
plt.ylim(-150,-50)

In [ ]:
from centerline.geometry import Centerline
from scipy.spatial import cKDTree

In [ ]:
class RoutingLayout():
    def __init__(self,device,border_tolerance,line_to_line_distance,max_parallel_lines):
        assert type(device)==shapely.geometry.polygon.Polygon
        self.device=device
        self.shaved_device=device.buffer(-border_tolerance)
        self.line_to_line_distance=line_to_line_distance
        self.max_parallel_lines=max_parallel_lines
        
        #create skeleton of the polygon (midlines)
        cline=Centerline(shapelypolygon)
        cline=shapely.ops.linemerge(cline.geometry)
        self.skeleton=self.remove_dangling_lines(cline)
        
        
    def remove_dangling_lines(self,obj):
        '''self.obj is a shapely multiline'''
        xy_s=[]
        for line in obj.geoms:
            for g in line.boundary.geoms:
                p=np.asarray(g.coords).T
                xy_s.append(p)
        xy_s=np.asarray(xy_s)[:,:,0] #kill last dimension
        tree=cKDTree(xy_s)
        points_with_neighbors=np.unique(np.concatenate(list(tree.query_pairs(r=1e-5)))) 
        points_without_neighbors = [el//2 for el in range(2*len(obj.geoms)) if el not in points_with_neighbors]
        #we collect 2 points for each line edges in the kdtree, so line indices (who dangle) are obtained by //2
        new_skel=[obj.geoms[el] for el in range(len(obj.geoms)) if el not in points_without_neighbors]
        return shapely.MultiLineString(new_skel)
    
    #get waypoint to check closest border to understand what radius to look at. Should it do a square instead?
    
    def lay_down_lines(self,d,n):
        collect=[]
        #d=self.line_to_line_distance
        #n=self.max_parallel_lines
        midline_polygon=self.skeleton.buffer(.1) #turn it into a polygon
        
        if n%2==0: #odd line number
            gap_sizes = np.arange(d/2.,d/2.+n/2*d+1,d) #both sides of midline get only half a gap, since midline will be removed
        else:
            gap_sizes = np.arange(d,int(n/2.)*d+1,d)
        
        for i in gap_sizes: #start distance d from mid line and buffer down
            for pol in midline_polygon.interiors:
                route_line=shapely.Polygon(pol).buffer(-i).buffer(-5).buffer(5) #Make line to polygon, buffer it down, grab its outline
                if (route_line.geom_type!='MultiPolygon'):
                    if self.shaved_device.contains(route_line.exterior):
                        collect.append(np.asarray(route_line.exterior.coords))
                    else:
                        left_over_line=route_line.exterior.intersection(self.shaved_device)
                        xys=self.get_coords(left_over_line)
                        if type(xys)==list:
                            for coords in xys:
                                collect.append(coords)
                        elif len(xys)>0:
                            collect.append(xys)

                #     collect.append(np.asarray( shapelypolygon.difference(shapely.Polygon(route_line)).exterior.coords))
            route_line=shapely.Polygon(midline_polygon.exterior).buffer(i).buffer(5).buffer(-5).exterior #Make line to polygon, buffer it down, grab its outline
            if shapelypolygon.contains(route_line):
                collect.append(np.asarray(route_line.coords))
        self.possible_routes=shapely.MultiLineString([shapely.LineString(el) for el in collect])
        if n%2!=0:
            self.possible_routes = self.skeleton.union(self.possible_routes) #put the midline as a route.
            
    def get_coords(self,obj):
        if hasattr(obj,'geoms'):
            coords=[]
            for g in obj.geoms:
                coords.append(np.asarray(g.coords))
        else:
            coords=np.asarray(obj.coords)
        return coords
    def make_grids_at_waypoints(self,rotation_angle=180):
        #All biffurcations in the skeleton indicate points at which routes need to jump to different lines.
        #to do that, we need to provide a local grid. This is done by cutting out all the lines around
        #a biffurcation point, and rotating them in place and adding them to the design. This creates
        #a criss-cross pattern.
        self.borders=shapely.MultiLineString([self.device.exterior]+[el for el in self.device.interiors])
        self.waypoints=self.skeleton.boundary #gets all end points of line segments. Check if not double counted
        
        self.lines_to_add_for_crisscross = []
        for wp in self.waypoints.geoms:
            x,y=np.asarray(wp.coords).T
            radius_to_border = wp.distance(self.borders)
            lines_around_wp = wp.buffer(radius_to_border).intersection(self.possible_routes) #make a circle around waypoint and collect all lines in it
            rotated=shapely.affinity.rotate(lines_around_wp,rotation_angle,origin=(x,y))
            #rotated_clean=self.remove_dangling_lines(rotated.union(lines_around_wp)) #remove dangler lines in the cross cross
            #rotated_clean=rotated.intersection(rotated_clean) #retrieve original extra lines, to not carry a copy of original 'lines around wp' lines inside the route lines
            #rotated_clean=unary_union([el for el in rotated_clean.geoms if el.geom_type=='LineString']) #points are not necessary here 
            #self.lines_to_add_for_crisscross.append(rotated_clean)#reduce number of segments if contiguous
            self.lines_to_add_for_crisscross.append(rotated)
        self.lines_to_add_for_crisscross=shapely.ops.linemerge(unary_union(self.lines_to_add_for_crisscross))

        #clean up these lines. boolean cut them, remove dangles, etc.
        

In [ ]:
router= RoutingLayout(shapelypolygon,border_tolerance=2,line_to_line_distance=3,max_parallel_lines=5)


In [ ]:
router.lay_down_lines(2,9)

In [ ]:
router.lay_down_lines(2,9)
router.make_grids_at_waypoints(180)

In [ ]:
crosses=router.lines_to_add_for_crisscross

In [ ]:
for el in router.possible_routes.geoms:
    x,y=np.asarray(el.coords).T
    plt.plot(x,y,color='k')
for el in crosses.geoms:
    x,y=np.asarray(el.coords).T
    plt.plot(x,y)

In [ ]:
len(router.possible_routes.geoms)

In [ ]:
np.arange(d,int(n/2.)*d+1,d)
int(n/2.)*d
np.arange(3,7,3)

In [ ]:
skel.boundary.geoms[0].distance(shapelypolygon.ext)

In [ ]:
borders=shapely.MultiLineString([shapelypolygon.exterior]+[el for el in shapelypolygon.interiors])

In [ ]:
skel.boundary.geoms[0].distance(borders)

In [ ]:
line=shapely.ops.linemerge(router.lines_to_add_for_crisscross[0]).geoms[3]

In [ ]:
unary_union(line.interpolate(np.linspace(0,1,12),normalized=True))

In [ ]:
unary_union( line.simplify(tolerance=.1).interpolate(np.linspace(0,1,7),normalized=True)) 

In [ ]:
unary_union( [shapely.Point(el) for el in line.simplify(tolerance=.1).coords] )

In [ ]:
#simplify is extremely powerful to subsample curve to within tolerance distance. 

In [ ]:
help(line.segmentize)

In [ ]:
import networkx as nx

In [ ]:
nx.__file__